In [1]:
!pip install torchmetrics
!pip install comet_ml torch torchvision tqdm

Defaulting to user installation because normal site-packages is not writeable

[notice] A new release of pip is available: 23.2.1 -> 23.3.1
[notice] To update, run: /usr/bin/python -m pip install --upgrade pip
Defaulting to user installation because normal site-packages is not writeable

[notice] A new release of pip is available: 23.2.1 -> 23.3.1
[notice] To update, run: /usr/bin/python -m pip install --upgrade pip


In [8]:
import sys
 
sys.path.insert(0, "../")

from EnsembleFramework import Framework

In [9]:
from torch_geometric.datasets import Planetoid
import torch_geometric.transforms as T
from torch_geometric.utils import add_self_loops

dataset_name = 'Cora'
split = "public"
dataset = Planetoid(root='/tmp/Cora', name=dataset_name, split=split)
dataset.transform = T.NormalizeFeatures()

features =  dataset[0].x
y =  dataset[0].y

test =  dataset[0].test_mask
train = dataset[0].train_mask
val =  dataset[0].val_mask

edge_index = dataset[0].edge_index 
edge_index = add_self_loops(edge_index)[0]

In [10]:
from torch.nn.functional import normalize
def user_function(kwargs):
    return  normalize(kwargs["original_features"] + kwargs["summed_neighbors"], p=2.0, dim = 1)
    
hops_list = [1,3,4,6,7,8,9,15, 20, 30, 40, 50]#[0,2,5,10, 15, 20, 30]
framework = Framework([user_function for i in hops_list], 
                     hops_list=hops_list, ## to obtain best for local neighborhood
                     clfs=[],
                     gpu_idx=0,
                     handle_nan=0.0,
                    attention_configs=[None for i in hops_list])
new_features_list = framework.get_features(features, edge_index, None)

In [11]:
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score
import numpy as np
from sklearn.model_selection import ParameterGrid
from tqdm.notebook import tqdm
from hyperopt import fmin, tpe, hp,STATUS_OK

penalty = ["l1","l2", None, "elasticnet"]
max_iter = [2**i for i in range(6, 15)]

lr_choices = {
    'penalty': penalty,
    'max_iter': max_iter,
    
}

space = {
    **{key: hp.choice(key, value) for key, value in lr_choices.items()},
    'tol': hp.loguniform('tol', -11, -3),
    'C': hp.uniform('C', 0.0, 10),
    'l1_ratio': hp.uniform('l1_ratio', 0.0, 1.0)
}

clf = LogisticRegression
# hops_to_params=dict({})
# hops_to_score=dict({})

for i, hops in tqdm(enumerate(hops_list)):
    new_features = new_features_list[i].cpu()
    
    def objective(params):
        model = clf(**params, random_state = 42, solver= "saga")
        model.fit(new_features[train], y[train])
        y_pred = model.predict(new_features[val])
        score = accuracy_score(y[val], y_pred)
        return {'loss': -score, 'status': STATUS_OK}
    
    best_params = fmin(objective, space, algo=tpe.suggest, max_evals=1_000)

    for key,value in lr_choices.items():
        best_params[key] = value[best_params[key]]

    best_model = clf(**best_params, random_state = 42, solver= "saga")
    best_model.fit(new_features[train], y[train])
    y_pred = best_model.predict(new_features[val])
    
    hops_to_params[hops] = best_params
    hops_to_score[hops] = accuracy_score(y[val], y_pred)

0it [00:00, ?it/s]


  0%|                                                                          | 0/1000 [00:00<?, ?trial/s, best loss=?]

/home/dwalke/.local/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:1172: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=l1)
  warnings.warn(




  0%|▏                                                           | 4/1000 [00:05<15:20,  1.08trial/s, best loss: -0.758]

/home/dwalke/.local/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:1172: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=l1)
  warnings.warn(

/home/dwalke/.local/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:1172: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=l1)
  warnings.warn(



...

/home/dwalke/.local/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:1172: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=None)
  warnings.warn(

/home/dwalke/.local/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:1193: UserWarning: Setting penalty=None will ignore the C and l1_ratio parameters
  warnings.warn(




100%|█████████████████████████████████████████████████████████▉| 999/1000 [54:50<00:01,  1.09s/trial, best loss: -0.824]

/home/dwalke/.local/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:1172: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=l1)
  warnings.warn(




100%|█████████████████████████████████████████████████████████| 1000/1000 [54:51<00:00,  3.29s/trial, best loss: -0.824]


/home/dwalke/.local/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:1172: UserWarning: l1_ratio parameter is only used when penalty is 'elasticnet'. Got (penalty=None)
  warnings.warn(
/home/dwalke/.local/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:1193: UserWarning: Setting penalty=None will ignore the C and l1_ratio parameters
  warnings.warn(


In [6]:
hops_to_params

{0: {'C': 3.346048903444868,
  'l1_ratio': 0.01220223988095433,
  'max_iter': 1024,
  'penalty': None,
  'tol': 0.011398278271416415},
 2: {'C': 6.552418536384322,
  'l1_ratio': 0.35616288828645437,
  'max_iter': 512,
  'penalty': 'l2',
  'tol': 0.02129975507663451},
 5: {'C': 3.886954615084303,
  'l1_ratio': 0.3160574463568011,
  'max_iter': 8192,
  'penalty': None,
  'tol': 0.03825901150144381},
 10: {'C': 4.268895952270713,
  'l1_ratio': 0.6429245814995024,
  'max_iter': 512,
  'penalty': None,
  'tol': 0.016167762825700257},
 15: {'C': 9.334260127671346,
  'l1_ratio': 0.6438450087129208,
  'max_iter': 16384,
  'penalty': None,
  'tol': 0.008342788591252898},
 20: {'C': 1.747367564486253,
  'l1_ratio': 0.14772016160343032,
  'max_iter': 1024,
  'penalty': None,
  'tol': 0.006981350357578392},
 30: {'C': 3.9252161926287337,
  'l1_ratio': 0.0011402047702883302,
  'max_iter': 128,
  'penalty': None,
  'tol': 0.002375637603020751}}

In [7]:
# hops_to_score = {0: 0.604, 2: 0.806, 5: 0.816, 10: 0.816, 15: 0.822, 20: 0.826, 30: 0.828}
# hops_to_score

{0: 0.604, 2: 0.806, 5: 0.816, 10: 0.816, 15: 0.822, 20: 0.826, 30: 0.828}

In [1]:
# hops_to_params = {0: {'C': 3.346048903444868,
#   'l1_ratio': 0.01220223988095433,
#   'max_iter': 1024,
#   'penalty': None,
#   'tol': 0.011398278271416415},
#  2: {'C': 6.552418536384322,
#   'l1_ratio': 0.35616288828645437,
#   'max_iter': 512,
#   'penalty': 'l2',
#   'tol': 0.02129975507663451},
#  5: {'C': 3.886954615084303,
#   'l1_ratio': 0.3160574463568011,
#   'max_iter': 8192,
#   'penalty': None,
#   'tol': 0.03825901150144381},
#  10: {'C': 4.268895952270713,
#   'l1_ratio': 0.6429245814995024,
#   'max_iter': 512,
#   'penalty': None,
#   'tol': 0.016167762825700257},
#  15: {'C': 9.334260127671346,
#   'l1_ratio': 0.6438450087129208,
#   'max_iter': 16384,
#   'penalty': None,
#   'tol': 0.008342788591252898},
#  20: {'C': 1.747367564486253,
#   'l1_ratio': 0.14772016160343032,
#   'max_iter': 1024,
#   'penalty': None,
#   'tol': 0.006981350357578392},
#  30: {'C': 3.9252161926287337,
#   'l1_ratio': 0.0011402047702883302,
#   'max_iter': 128,
#   'penalty': None,
#   'tol': 0.002375637603020751}}

In [12]:
import pandas as pd
df = pd.DataFrame(columns=["best_params"], index=hops_to_params.keys())
df["best_params"] = hops_to_params.values()
df.to_csv("normalized_origin_features_plus_summed_neighbors_wo_attn.csv")
df

best_params
0   {'C': 3.346048903444868, 'l1_ratio': 0.0122022...
2   {'C': 6.552418536384322, 'l1_ratio': 0.3561628...
5   {'C': 3.886954615084303, 'l1_ratio': 0.3160574...
10  {'C': 4.268895952270713, 'l1_ratio': 0.6429245...
15  {'C': 0.6168486310332411, 'l1_ratio': 0.163002...
20  {'C': 6.4371186505294355, 'l1_ratio': 0.278466...
30  {'C': 4.080036163461636, 'l1_ratio': 0.1621388...
1   {'C': 1.2938518450759626, 'l1_ratio': 0.272221...
3   {'C': 3.4570275594935573, 'l1_ratio': 0.975983...
4   {'C': 9.251257441253045, 'l1_ratio': 0.1010454...
6   {'C': 0.07667384778658182, 'l1_ratio': 0.48892...
7   {'C': 8.157961903086694, 'l1_ratio': 0.9959290...
8   {'C': 5.3785092461893305, 'l1_ratio': 0.241756...
9   {'C': 0.9767421484439999, 'l1_ratio': 0.426927...
40  {'C': 1.8223335304772958, 'l1_ratio': 0.215554...
50  {'C': 0.9929601670037467, 'l1_ratio': 0.324801...

In [8]:
raise Exception

Exception: 

In [ ]:
hops_to_params

In [ ]:
hops_to_score